# AI_FORECAST DBSQL Function

AI_FORECAST is a table-valued function designed to extrapolate time series data into the future. In its most general form, AI_FORECAST accepts __grouped, multivariate, mixed-granularity data,__ and forecasts that data up to some horizon in the future.


AI_FORECAST is an all-in-one function for doing out-of-sample predictions on a large number of time series simultaneously. AI_FORECAST is useful for

- On-the-fly applications where training and persisting models is not required (e.g. dashboards, investigations)
- Scenarios where model persistence is complicated or cumbersome (e.g. generating forecasts for multiple grouping set rollups over the same dataset, or if some dimensions have a few months of data & others have years of data)
- Forecasting “at scale” in the sense that many independent models are trained and evaluated simultaneously.

### Prerequisites 
Standard compute clusters or SQL warehouses running DBR 15.1+. The function is not yet available on serverless.

### Setup
AI_FORECAST can be enabled in standard compute environments (i.e. not SQL warehouses) at a session level via the Spark configuration.

`SET spark.databricks.sql.functions.aiForecast.enabled = TRUE`

### API

```
SELECT ... FROM AI_FORECAST(
  observed TABLE,
  horizon DATE | TIMESTAMP | STRING,
  time_col STRING,
  value_col STRING | ARRAY<STRING>,
  group_col STRING | ARRAY<STRING> | NULL DEFAULT NULL,
  prediction_interval_width DOUBLE DEFAULT 0.95,
  frequency STRING DEFAULT 'auto',
  seed INTEGER | NULL DEFAULT NULL,
  parameters STRING DEFAULT '{}' -- * New in DBR 15.3 *
)

```


# Examples

In [0]:
SET spark.databricks.sql.functions.aiForecast.enabled = TRUE

key value spark.databricks.sql.functions.aiForecast.enabled TRUE

### Forecast until a Specified Date.

In [0]:
SELECT * FROM samples.nyctaxi.trips order by tpep_pickup_datetime desc

tpep_pickup_datetime tpep_dropoff_datetime trip_distance fare_amount pickup_zip dropoff_zip 2016-02-29T23:51:20Z 2016-02-29T23:57:41Z 0.91 6.5 10153 10065 2016-02-29T23:51:06Z 2016-02-29T23:59:38Z 1.4 7.5 10154 10019 2016-02-29T23:50:27Z 2016-02-29T23:54:25Z 1.35 6.0 11238 11205 2016-02-29T23:39:15Z 2016-02-29T23:55:24Z 2.8 12.5 10003 10038 2016-02-29T23:33:22Z 2016-02-29T23:38:56Z 0.8 5.5 10001 10011 2016-02-29T23:32:16Z 2016-02-29T23:49:57Z 8.72 25.5 11371 10021 2016-02-29T23:29:04Z 2016-02-29T23:34:08Z 1.0 6.0 10003 10001 2016-02-29T23:23:23Z 2016-02-29T23:42:33Z 3.5 15.5 10001 10162 2016-02-29T23:23:16Z 2016-02-29T23:26:03Z 0.51 4.0 11231 11201 2016-02-29T23:21:38Z 2016-02-29T23:34:44Z 2.33 11.0 11211 11222 2016-02-29T23:21:34Z 2016-02-29T23:39:52Z 7.5 24.0 11371 10026 2016-02-29T23:05:54Z 2016-02-29T23:12:18Z 1.28 6.5 10018 10111 2016-02-29T22:58:10Z 2016-02-29T22:59:58Z 0.7 4.0 10018 10199 2016-02-29T22:46:53Z 2016-02-29T22:52:01Z 1.0 5.5 10011 10009 2016-02-29T22:46:01Z 2016-02-29T22:56:13Z 1.4 8.5 10103 10017 2016-02-29T22:42:54Z 2016-02-29T23:14:59Z 18.91 50.5 11422 11201 2016-02-29T22:41:15Z 2016-02-29T22:56:37Z 3.28 13.5 10103 10025 2016-02-29T22:40:32Z 2016-02-29T22:56:26Z 3.7 14.0 10119 10028 2016-02-29T22:37:52Z 2016-02-29T22:50:13Z 8.31 23.0 11371 10017 2016-02-29T22:36:48Z 2016-02-29T22:54:22Z 6.63 21.0 10022 11201 2016-02-29T22:28:14Z 2016-02-29T22:33:57Z 1.47 6.5 10027 10039 2016-02-29T22:27:40Z 2016-02-29T22:46:39Z 7.7 24.5 10020 10039 2016-02-29T22:25:33Z 2016-02-29T22:38:09Z 3.5 13.5 10001 11222 2016-02-29T22:23:40Z 2016-02-29T22:48:30Z 9.4 29.0 10154 11238 2016-02-29T22:21:57Z 2016-02-29T22:24:45Z 0.6 4.5 10001 10011 2016-02-29T22:19:22Z 2016-02-29T22:29:32Z 2.85 10.5 10110 10044 2016-02-29T22:14:02Z 2016-02-29T22:29:31Z 2.81 13.0 10028 10017 2016-02-29T22:11:57Z 2016-02-29T22:21:46Z 2.4 9.5 10011 10020 2016-02-29T22:10:30Z 2016-02-29T22:19:31Z 1.83 8.5 10110 10069 2016-02-29T22:10:09Z 2016-02-29T23:02:35Z 18.4 52.0 11422 10018 2016-02-29T22:06:03Z 2016-02-29T22:17:13Z 2.9 11.5 10002 11211 2016-02-29T22:02:25Z 2016-02-29T22:16:16Z 2.71 12.0 10014 10103 2016-02-29T21:56:33Z 2016-02-29T22:00:56Z 1.5 6.5 10065 10028 2016-02-29T21:44:08Z 2016-02-29T22:12:55Z 7.32 25.5 10003 11212 2016-02-29T21:43:52Z 2016-02-29T22:01:52Z 5.1 18.0 10018 10162 2016-02-29T21:41:54Z 2016-02-29T21:57:17Z 5.8 19.0 10103 10006 2016-02-29T21:31:18Z 2016-02-29T21:37:42Z 1.6 7.0 10001 10022 2016-02-29T21:27:49Z 2016-02-29T21:35:41Z 1.9 8.0 10110 10021 2016-02-29T21:25:58Z 2016-02-29T21:31:37Z 1.3 6.5 10027 10025 2016-02-29T21:19:39Z 2016-02-29T21:36:12Z 6.27 20.5 10282 11211 2016-02-29T21:07:58Z 2016-02-29T21:13:25Z 0.8 6.0 10019 10018 2016-02-29T21:05:16Z 2016-02-29T21:24:32Z 4.5 16.5 10069 10002 2016-02-29T21:03:41Z 2016-02-29T21:14:21Z 2.76 11.0 10003 10022 2016-02-29T21:02:28Z 2016-02-29T21:15:38Z 3.93 13.5 10162 10011 2016-02-29T20:54:59Z 2016-02-29T21:25:56Z 6.09 24.0 10012 11102 2016-02-29T20:51:29Z 2016-02-29T21:01:18Z 1.7 8.5 10111 10021 2016-02-29T20:48:49Z 2016-02-29T21:04:21Z 1.96 11.5 10110 10069 2016-02-29T20:38:30Z 2016-02-29T20:42:32Z 0.91 5.0 10009 10003 2016-02-29T20:37:38Z 2016-02-29T20:45:34Z 0.9 7.0 10065 10021 2016-02-29T20:32:48Z 2016-02-29T20:41:55Z 1.15 7.5 10103 10022 2016-02-29T20:32:44Z 2016-02-29T20:59:40Z 6.21 21.0 10021 10026 2016-02-29T20:29:52Z 2016-02-29T20:32:15Z 0.57 4.0 10014 10011 2016-02-29T20:19:14Z 2016-02-29T20:47:13Z 6.39 23.0 10278 10026 2016-02-29T20:16:49Z 2016-02-29T20:26:01Z 1.92 9.0 10023 10018 2016-02-29T20:11:52Z 2016-02-29T20:24:23Z 2.65 10.5 10011 10006 2016-02-29T20:08:42Z 2016-02-29T20:13:41Z 1.0 5.5 10001 10003 2016-02-29T20:06:55Z 2016-02-29T20:29:01Z 5.25 19.0 10022 11211 2016-02-29T20:05:26Z 2016-02-29T20:19:11Z 4.21 14.5 10022 11222 2016-02-29T19:48:15Z 2016-02-29T20:09:25Z 4.3 17.0 10154 10013 2016-02-29T19:47:57Z 2016-02-29T19:52:42Z 0.81 5.5 10044 10021 2016-02-29T19:47:43Z 2016-02-29T20:12:34Z 4.6 18.5 10011 11205 2016-02-29T19:45:21Z 2016-02-29T20:03:32Z 3.0 14.0 10003 10

##### Let's say we wanted to forecast revenue (sum of fair_amount) per day.

In [0]:
WITH
aggregated AS (
  SELECT
    DATE(tpep_pickup_datetime) AS ds,
    SUM(fare_amount) AS revenue
  FROM
    samples.nyctaxi.trips
  GROUP BY
    1
)
SELECT * FROM AI_FORECAST(
  TABLE(aggregated),
  horizon => '2016-03-31',
  time_col => 'ds',
  value_col => 'revenue'
)


ds revenue_forecast revenue_upper revenue_lower 2016-03-01 4913.364710590872 5092.238161490353 900.9210677797578 2016-03-02 5206.637086933598 7264.220917778914 1194.1934441224835 2016-03-03 5804.4132960390025 5806.025692797726 1791.969653227888 2016-03-04 5662.675824170121 7720.619871007284 1650.2321813590065 2016-03-05 5146.320389718501 7204.275020292225 1133.8767469073869 2016-03-06 4839.87083907125 6897.825780367234 827.4271962601356 2016-03-07 4822.592401290079 6880.549366068541 810.1487584789643 2016-03-08 5130.882708186111 7152.853560793545 1118.4390653749965 2016-03-09 5424.155084528837 7482.111417161024 1411.7114417177222 2016-03-10 6021.931293634252 6673.050186998387 2009.4876508231378 2016-03-11 5880.193821765368 7938.150764783004 1867.7501789542534 2016-03-12 5363.838387313747 7421.795348262283 1351.3947445026333 2016-03-13 5057.388836666495 7115.345798141452 1044.9451938553807 2016-03-14 5040.110398885325 7098.06736378843 1027.6667560742103 2016-03-15 5348.40070578136 7406.295620500139 1335.9570629702453 2016-03-16 5641.673082124101 7699.630045956235 1629.2294393129864 2016-03-17 6239.4492912295 8289.900523273984 2227.0056484183906 2016-03-18 6097.711819360629 8155.668784226868 2085.2681765495154 2016-03-19 5581.35638490899 7639.313349805607 1568.9127420979607 2016-03-20 5274.906834261744 7332.863799159253 1262.4631914506294 2016-03-21 5257.628396480574 7315.585361383892 1245.18475366946 2016-03-22 5565.918703376622 7623.875563152522 1553.4750605655076 2016-03-23 5859.191079719327 7917.14804462083 1846.7474369082124 2016-03-24 6456.967288824747 8514.911491188617 2444.5236460153856 2016-03-25 6315.229816955866 8373.18678185912 2302.7861741448914 2016-03-26 5798.874382504236 7856.831347407542 1786.4307397236144 2016-03-27 5492.424831856988 7550.381796760295 1479.9811890458736 2016-03-28 5475.14639407582 7533.103358979138 1462.702751264706 2016-03-29 5783.436700971865 7841.393665697078 1770.9930581607518 2016-03-30 6076.709077314591 8134.666042217905 2064.2654345034766

Databricks visualization. Run in Databricks to view.

### A slightly more complex example.

It is very common for tables to not materialize 0s or empty entries. If the values of the missing entries can be inferred (e.g. 0, 100%, etc.) then these values should be coalesced prior to calling the forecast function. If the values are truly missing or unknown, then they can be left empty.

For very sparse data (e.g. >50% missing entries), it is best practice to provide a frequency value explicitly. Two entries 35 days apart will be inferred as a time series with granularity 35D, rather than a daily series with 34 missing entries.


Here's an example of missing dates in the `nyctaxi.trips` table.

In [0]:
SELECT
    DATE(tpep_pickup_datetime) AS ds,
    dropoff_zip,
    SUM(fare_amount) AS revenue,
    COUNT(*) AS n_trips
  FROM
    samples.nyctaxi.trips
  WHERE dropoff_zip = 7114
  GROUP BY
    1, 2
  ORDER BY ds 


ds dropoff_zip revenue n_trips 2016-01-01 7114 66.0 1 2016-01-03 7114 64.5 1 2016-01-04 7114 105.0 1 2016-01-06 7114 61.5 1 2016-01-08 7114 122.5 2 2016-01-09 7114 53.5 1 2016-01-10 7114 67.0 1 2016-01-11 7114 78.5 1 2016-01-12 7114 71.0 1 2016-01-21 7114 56.5 1 2016-01-22 7114 172.0 2 2016-01-25 7114 85.5 1 2016-01-28 7114 69.5 1 2016-01-29 7114 70.5 1 2016-02-01 7114 62.5 1 2016-02-04 7114 72.0 1 2016-02-06 7114 69.0 1 2016-02-11 7114 207.5 3 2016-02-13 7114 64.0 1 2016-02-21 7114 56.0 1 2016-02-22 7114 95.0 1 2016-02-24 7114 64.0 1 2016-02-25 7114 62.0 1 2016-02-26 7114 74.0 1 2016-02-28 7114 66.0 1

##### Let's say we wanted to forecast revenue AND number of trips for each dropoff zip code.

In [0]:
-- Generate the aggregated table from the nyctaxi.trips
WITH
aggregated AS (
  SELECT
    DATE(tpep_pickup_datetime) AS ds,
    dropoff_zip,
    SUM(fare_amount) AS revenue,
    COUNT(*) AS n_trips
  FROM
    samples.nyctaxi.trips
  GROUP BY
    1, 2
),
-- Generate the full series of missing dates for each zip code
spine AS (
  SELECT all_dates.ds, all_zipcodes.dropoff_zip
  FROM (SELECT DISTINCT ds FROM aggregated) all_dates
  CROSS JOIN (SELECT DISTINCT dropoff_zip FROM aggregated) all_zipcodes
)
-- Perform forecast on the spine and aggregated table
SELECT * FROM AI_FORECAST(
-- Input table fills in zero for dates that were originally empty
  TABLE(
    SELECT
      spine.*,
      COALESCE(aggregated.revenue, 0) AS revenue,
      COALESCE(aggregated.n_trips, 0) AS n_trips
    FROM spine LEFT JOIN aggregated USING (ds, dropoff_zip)
  ),
  horizon => '2016-03-31',
  time_col => 'ds',
  value_col => ARRAY('revenue', 'n_trips'),
  group_col => 'dropoff_zip',
  prediction_interval_width => 0.9,
  parameters => '{"global_floor": 0}'
)
order by dropoff_zip,ds 


ds dropoff_zip revenue_forecast revenue_upper revenue_lower n_trips_forecast n_trips_upper n_trips_lower 2016-03-01 7002 5.830807389685071E-9 5.830807575898092E-9 0.0 3.751101133954946E-9 3.7511012008475565E-9 0.0 2016-03-02 7002 7.724019338004879E-9 7.724019480299643E-9 0.0 4.9584357236926724E-9 4.984307258761572E-9 0.0 2016-03-03 7002 1.0223942223693747E-8 1.0223942363623074E-8 0.0 6.547250447116308E-9 2.8155256000339153E-6 0.0 2016-03-04 7002 4.896544814955026E-6 4.951466908084134E-6 9.053182831515639E-11 1.8945461005526096E-6 1.8998412087594537E-6 8.318459876382042E-11 2016-03-05 7002 2.4600731222833474E-8 2.460073127958457E-8 0.0 1.4633115426471153E-8 1.4633305637667994E-8 0.0 2016-03-06 7002 3.3748390477429E-8 3.3748390517157313E-8 0.0 1.96827484028089E-8 1.968352621499138E-8 0.0 2016-03-07 7002 4.628072309266662E-8 4.62807231200813E-8 0.0 2.6417820856655762E-8 2.6419012253789127E-8 0.0 2016-03-08 7002 9.273902674990348E-8 9.2739026750261E-8 0.0 4.5745265778696525E-8 4.5745265778786754E-8 0.0 2016-03-09 7002 1.22374781743227E-7 1.2237478174350028E-7 0.0 6.011792783691042E-8 6.011796262661401E-8 0.0 2016-03-10 7002 1.6150780232670372E-7 1.6150780232697242E-7 0.0 7.903190353758599E-8 7.911004250928379E-8 0.0 2016-03-11 7002 7.665046527565563E-5 7.6650570232401E-5 2.8825262625892927E-9 2.2554632014322473E-5 2.255463914210746E-5 2.0807129439845284E-9 2016-03-12 7002 3.865576160822754E-7 3.865576160823846E-7 0.0 1.7528973113934193E-7 1.7528973139570664E-7 0.0 2016-03-13 7002 5.297522481847295E-7 5.297522481848057E-7 0.0 2.3540286705362762E-7 2.3540286810194198E-7 0.0 2016-03-14 7002 7.259295114909753E-7 7.259295114910281E-7 0.0 3.15580243846724E-7 3.1558024545245293E-7 0.0 2016-03-15 7002 1.4531734451737464E-6 1.4531734451737464E-6 0.0 5.456629704366908E-7 5.456629704366908E-7 0.0 2016-03-16 7002 1.917082398845839E-6 1.917082398845839E-6 0.0 7.167617001471984E-7 7.167617001940876E-7 0.0 2016-03-17 7002 2.5296586141975566E-6 2.5296586141975566E-6 0.0 9.419223003931435E-7 9.41922405661922E-7 0.0 2016-03-18 7002 0.0011998641701495372 0.0011998641703511292 4.6587544760860686E-8 2.68501725269387E-4 2.6850172527899386E-4 2.5860202296941292E-8 2016-03-19 7002 6.05251887697634E-6 6.05251887697634E-6 1.355115672409036E-10 2.08781941817433E-6 2.0878194181746748E-6 1.0187129238745868E-10 2016-03-20 7002 8.294043412627767E-6 8.294043412627767E-6 2.2273083003113357E-10 2.8034336274410253E-6 2.8034336274424394E-6 1.7106072758212286E-10 2016-03-21 7002 1.1364941689898961E-5 1.1364941689898961E-5 3.4222159606442755E-10 3.75790171868621E-6 3.757901718688373E-6 2.6334384226799134E-10 2016-03-22 7002 2.274899356963223E-5 2.274899356963223E-5 7.851828917022805E-10 6.4969115199613176E-6 6.4969115199613176E-6 5.281660588881833E-10 2016-03-23 7002 3.00108810209723E-5 3.00108810209723E-5 1.067747931655104E-9 8.53374889844834E-6 8.533748898448402E-6 7.25098464611843E-10 2016-03-24 7002 3.9599959860780436E-5 3.9599959860780436E-5 1.4408655906159512E-9 1.1214163460962723E-5 1.1214163461104596E-5 9.842553780247322E-10 2016-03-25 7002 0.018782304526248274 0.018782304526248655 7.307324031023939E-7 0.0031963681888013355 0.0031963681888013493 3.0894209798037324E-7 2016-03-26 7002 9.474572614229904E-5 9.474572614229904E-5 3.5866253200222548E-9 2.4855445809153894E-5 2.4855445809153894E-5 2.3031680110894792E-9 2016-03-27 7002 1.2983385877797103E-4 1.2983385877797103E-4 4.951928716212882E-9 3.3374444006728874E-5 3.3374444006728874E-5 3.1268306299727628E-9 2016-03-28 7002 1.7790475175718707E-4 1.7790475175718707E-4 6.8224002549494964E-9 4.473686784302396E-5 4.473686784302396E-5 4.225410950899317E-9 2016-03-29 7002 3.56107183153462E-4 3.56107183153462E-4 1.3756379538515398E-8 7.734329077042123E-5 7.734329077042123E-5 7.3779754987402846E-9 2016-03-30 7002 4.697825259950571E-4 4.697825259950571E-4 1.8179565384745878E-8 1.0159073266214956E-4 1.0159073266214956E-4 9.72234874857223E-9 2016-03-01 7008 0.0 0.02394913630530704 0.0 0.0 4.881570261929024E-4 0.0 2016-03-02 

###### To help better visualize what the `spine` table looks like:

In [0]:
WITH
aggregated AS (
  SELECT
    DATE(tpep_pickup_datetime) AS ds,
    dropoff_zip,
    SUM(fare_amount) AS revenue,
    COUNT(*) AS n_trips
  FROM
    samples.nyctaxi.trips
  GROUP BY
    1, 2
),
-- Generate the aggregated table from the nyctaxi.trips
spine AS (
  SELECT all_dates.ds, all_zipcodes.dropoff_zip
  FROM (SELECT DISTINCT ds FROM aggregated) all_dates
  CROSS JOIN (SELECT DISTINCT dropoff_zip FROM aggregated) all_zipcodes
)SELECT * FROM spine where dropoff_zip = 7114
order by ds asc

ds dropoff_zip 2016-01-01 7114 2016-01-02 7114 2016-01-03 7114 2016-01-04 7114 2016-01-05 7114 2016-01-06 7114 2016-01-07 7114 2016-01-08 7114 2016-01-09 7114 2016-01-10 7114 2016-01-11 7114 2016-01-12 7114 2016-01-13 7114 2016-01-14 7114 2016-01-15 7114 2016-01-16 7114 2016-01-17 7114 2016-01-18 7114 2016-01-19 7114 2016-01-20 7114 2016-01-21 7114 2016-01-22 7114 2016-01-23 7114 2016-01-24 7114 2016-01-25 7114 2016-01-26 7114 2016-01-27 7114 2016-01-28 7114 2016-01-29 7114 2016-01-30 7114 2016-01-31 7114 2016-02-01 7114 2016-02-02 7114 2016-02-03 7114 2016-02-04 7114 2016-02-05 7114 2016-02-06 7114 2016-02-07 7114 2016-02-08 7114 2016-02-09 7114 2016-02-10 7114 2016-02-11 7114 2016-02-12 7114 2016-02-13 7114 2016-02-14 7114 2016-02-15 7114 2016-02-16 7114 2016-02-17 7114 2016-02-18 7114 2016-02-19 7114 2016-02-20 7114 2016-02-21 7114 2016-02-22 7114 2016-02-23 7114 2016-02-24 7114 2016-02-25 7114 2016-02-26 7114 2016-02-27 7114 2016-02-28 7114 2016-02-29 7114

###### To help better visualize what the input table looks like:

In [0]:
-- Generate the aggregated table from the nyctaxi.trips
WITH
aggregated AS (
  SELECT
    DATE(tpep_pickup_datetime) AS ds,
    dropoff_zip,
    SUM(fare_amount) AS revenue,
    COUNT(*) AS n_trips
  FROM
    samples.nyctaxi.trips
  GROUP BY
    1, 2
),
-- Generate the full series of missing dates for each zip code
spine AS (
  SELECT all_dates.ds, all_zipcodes.dropoff_zip
  FROM (SELECT DISTINCT ds FROM aggregated) all_dates
  CROSS JOIN (SELECT DISTINCT dropoff_zip FROM aggregated) all_zipcodes
)
-- Perform forecast on the spine and aggregated table
SELECT
  spine.*,
  COALESCE(aggregated.revenue, 0) AS revenue,
  COALESCE(aggregated.n_trips, 0) AS n_trips
FROM spine LEFT JOIN aggregated USING (ds, dropoff_zip)
where dropoff_zip = 7114
order by ds asc


ds dropoff_zip revenue n_trips 2016-01-01 7114 66.0 1 2016-01-02 7114 0.0 0 2016-01-03 7114 64.5 1 2016-01-04 7114 105.0 1 2016-01-05 7114 0.0 0 2016-01-06 7114 61.5 1 2016-01-07 7114 0.0 0 2016-01-08 7114 122.5 2 2016-01-09 7114 53.5 1 2016-01-10 7114 67.0 1 2016-01-11 7114 78.5 1 2016-01-12 7114 71.0 1 2016-01-13 7114 0.0 0 2016-01-14 7114 0.0 0 2016-01-15 7114 0.0 0 2016-01-16 7114 0.0 0 2016-01-17 7114 0.0 0 2016-01-18 7114 0.0 0 2016-01-19 7114 0.0 0 2016-01-20 7114 0.0 0 2016-01-21 7114 56.5 1 2016-01-22 7114 172.0 2 2016-01-23 7114 0.0 0 2016-01-24 7114 0.0 0 2016-01-25 7114 85.5 1 2016-01-26 7114 0.0 0 2016-01-27 7114 0.0 0 2016-01-28 7114 69.5 1 2016-01-29 7114 70.5 1 2016-01-30 7114 0.0 0 2016-01-31 7114 0.0 0 2016-02-01 7114 62.5 1 2016-02-02 7114 0.0 0 2016-02-03 7114 0.0 0 2016-02-04 7114 72.0 1 2016-02-05 7114 0.0 0 2016-02-06 7114 69.0 1 2016-02-07 7114 0.0 0 2016-02-08 7114 0.0 0 2016-02-09 7114 0.0 0 2016-02-10 7114 0.0 0 2016-02-11 7114 207.5 3 2016-02-12 7114 0.0 0 2016-02-13 7114 64.0 1 2016-02-14 7114 0.0 0 2016-02-15 7114 0.0 0 2016-02-16 7114 0.0 0 2016-02-17 7114 0.0 0 2016-02-18 7114 0.0 0 2016-02-19 7114 0.0 0 2016-02-20 7114 0.0 0 2016-02-21 7114 56.0 1 2016-02-22 7114 95.0 1 2016-02-23 7114 0.0 0 2016-02-24 7114 64.0 1 2016-02-25 7114 62.0 1 2016-02-26 7114 74.0 1 2016-02-27 7114 0.0 0 2016-02-28 7114 66.0 1 2016-02-29 7114 0.0 0

### Daily + Hourly Forecasting
AI_FORECAST can be used to generate forecasts at multiple granularities spanning the same window of time.


In [0]:
SELECT * FROM AI_FORECAST(
-- Daily aggragtions of revenue
  TABLE(
    SELECT
      DATE_TRUNC('DAY', tpep_pickup_datetime) AS ts,
      ANY_VALUE('DAY') AS granularity,
      SUM(fare_amount) AS revenue
    FROM
      samples.nyctaxi.trips
    GROUP BY
      1
    
    UNION ALL
-- Hourly aggragtions of revenue
    SELECT
      DATE_TRUNC('HOUR', tpep_pickup_datetime) AS ts,
      ANY_VALUE('HOUR') AS granularity,
      SUM(fare_amount) AS revenue
    FROM
      samples.nyctaxi.trips
    GROUP BY
      1
  ),
  horizon => '2016-03-31',
  time_col => 'ts',
  value_col => 'revenue',
  group_col => 'granularity'
)


ts granularity revenue_forecast revenue_upper revenue_lower 2016-03-01T00:00:00Z DAY 4913.364710590872 5092.238161490353 900.9210677797578 2016-03-02T00:00:00Z DAY 5206.637086933598 7264.220917778914 1194.1934441224835 2016-03-03T00:00:00Z DAY 5804.4132960390025 5806.025692797726 1791.969653227888 2016-03-04T00:00:00Z DAY 5662.675824170121 7720.619871007284 1650.2321813590065 2016-03-05T00:00:00Z DAY 5146.320389718501 7204.275020292225 1133.8767469073869 2016-03-06T00:00:00Z DAY 4839.87083907125 6897.825780367234 827.4271962601356 2016-03-07T00:00:00Z DAY 4822.592401290079 6880.549366068541 810.1487584789643 2016-03-08T00:00:00Z DAY 5130.882708186111 7152.853560793545 1118.4390653749965 2016-03-09T00:00:00Z DAY 5424.155084528837 7482.111417161024 1411.7114417177222 2016-03-10T00:00:00Z DAY 6021.931293634252 6673.050186998387 2009.4876508231378 2016-03-11T00:00:00Z DAY 5880.193821765368 7938.150764783004 1867.7501789542534 2016-03-12T00:00:00Z DAY 5363.838387313747 7421.795348262283 1351.3947445026333 2016-03-13T00:00:00Z DAY 5057.388836666495 7115.345798141452 1044.9451938553807 2016-03-14T00:00:00Z DAY 5040.110398885325 7098.06736378843 1027.6667560742103 2016-03-15T00:00:00Z DAY 5348.40070578136 7406.295620500139 1335.9570629702453 2016-03-16T00:00:00Z DAY 5641.673082124101 7699.630045956235 1629.2294393129864 2016-03-17T00:00:00Z DAY 6239.4492912295 8289.900523273984 2227.0056484183906 2016-03-18T00:00:00Z DAY 6097.711819360629 8155.668784226868 2085.2681765495154 2016-03-19T00:00:00Z DAY 5581.35638490899 7639.313349805607 1568.9127420979607 2016-03-20T00:00:00Z DAY 5274.906834261744 7332.863799159253 1262.4631914506294 2016-03-21T00:00:00Z DAY 5257.628396480574 7315.585361383892 1245.18475366946 2016-03-22T00:00:00Z DAY 5565.918703376622 7623.875563152522 1553.4750605655076 2016-03-23T00:00:00Z DAY 5859.191079719327 7917.14804462083 1846.7474369082124 2016-03-24T00:00:00Z DAY 6456.967288824747 8514.911491188617 2444.5236460153856 2016-03-25T00:00:00Z DAY 6315.229816955866 8373.18678185912 2302.7861741448914 2016-03-26T00:00:00Z DAY 5798.874382504236 7856.831347407542 1786.4307397236144 2016-03-27T00:00:00Z DAY 5492.424831856988 7550.381796760295 1479.9811890458736 2016-03-28T00:00:00Z DAY 5475.14639407582 7533.103358979138 1462.702751264706 2016-03-29T00:00:00Z DAY 5783.436700971865 7841.393665697078 1770.9930581607518 2016-03-30T00:00:00Z DAY 6076.709077314591 8134.666042217905 2064.2654345034766 2016-03-01T00:00:00Z HOUR 161.07769391397855 520.2597160038915 -97.48377010370146 2016-03-01T01:00:00Z HOUR 116.10848105766334 488.25173745525444 -134.0588951645366 2016-03-01T02:00:00Z HOUR 100.81075723560815 473.4243259494188 -152.20038249093054 2016-03-01T03:00:00Z HOUR 89.29726301482602 457.13999901298405 -165.54167191610497 2016-03-01T04:00:00Z HOUR 70.46834320424047 432.78925676432584 -170.5498828867141 2016-03-01T05:00:00Z HOUR 74.38979812681652 443.72460277497197 -142.79350517575074 2016-03-01T06:00:00Z HOUR 121.09219532139635 492.1373591100025 -100.47527874091308 2016-03-01T07:00:00Z HOUR 184.90213492580588 553.665715864311 -66.93596230681928 2016-03-01T08:00:00Z HOUR 227.96064749558 592.2052201713108 -38.775938728512386 2016-03-01T09:00:00Z HOUR 239.20181798547338 593.9733541380688 -20.043016427838836 2016-03-01T10:00:00Z HOUR 230.63784393661675 543.9333806150498 4.155832539757199 2016-03-01T11:00:00Z HOUR 221.77426643815159 488.3722724744001 33.94350106482216 2016-03-01T12:00:00Z HOUR 230.40153448826752 541.3067109818167 51.87453358350788 2016-03-01T13:00:00Z HOUR 253.89962962662685 590.2645435660078 62.62510366508178 2016-03-01T14:00:00Z HOUR 264.7030339733018 576.3456373558365 60.927345687147294 2016-03-01T15:00:00Z HOUR 249.55945357553688 561.3061335164682 42.79154268053421 2016-03-01T16:00:00Z HOUR 238.051834916907 598.4303249371044 37.55106116486428 2016-03-01T17:00:00Z HOUR 259.04591304641576 627.1670076982298 71.16083340781421 2016-03-01T18:00:00Z HOUR 289.0011573048731 636.5242811681878 114.96303088553691 2016-

Databricks visualization. Run in Databricks to view.

### Investigations
AI_FORECAST can be used to perform drill-down investigations. Join forecasting results with the original table to compute residuals. Pair this functionality with grouping set rollups to quickly isolate unexpected changes.

In the sample data below we have introduce an anomaly for all CA/Rural UIDs on 2023-01-31.


In [0]:
CREATE OR REPLACE TEMPORARY VIEW
hierarchical_data_with_an_anomalous_date
AS
WITH
-- Create the dimensions for the dataset
dimensions AS (
  SELECT
    country, population, uid, 10 * RAND() AS intercept, RAND() AS slope
  LATERAL VIEW
    EXPLODE(ARRAY('US', 'CA', 'UK', 'IN')) t1 AS country
  LATERAL VIEW
    EXPLODE(ARRAY('Urban', 'Rural', 'Suburban')) t2 AS population
  LATERAL VIEW
    EXPLODE(SEQUENCE(0, 10)) t3 AS uid
),
-- Create the timestamps for the dataset
dim_times AS (
  SELECT dimensions.*, ts, DATEDIFF(HOUR, '2023-01-01', ts) AS x
  FROM dimensions
  LATERAL VIEW
    EXPLODE(SEQUENCE(
      TIMESTAMP('2023-01-01'),
      TIMESTAMP('2023-02-01'),
      INTERVAL 1 HOUR
    )) t AS ts
)
-- Create the value column
SELECT
  dim_times.*,
  (intercept + (slope * x) + RANDN())
  * IF(
      -- Introduce an anomaly for all CA/Rural UIDs on 2023-01-31
      DATE(ts) = '2023-01-31'
      AND country = 'CA'
      AND population = 'Rural',
      0.75,
      1.0
  ) AS y
FROM
  dim_times;
SELECT country,population,uid, ts, y FROM hierarchical_data_with_an_anomalous_date;


country population uid ts y US Urban 0 2023-01-01T00:00:00Z 7.713485518088246 US Urban 0 2023-01-01T01:00:00Z 8.271630002988095 US Urban 0 2023-01-01T02:00:00Z 9.06897942577231 US Urban 0 2023-01-01T03:00:00Z 10.752951540626558 US Urban 0 2023-01-01T04:00:00Z 8.446783877678373 US Urban 0 2023-01-01T05:00:00Z 10.420320505129027 US Urban 0 2023-01-01T06:00:00Z 10.566414334928684 US Urban 0 2023-01-01T07:00:00Z 12.338550404938387 US Urban 0 2023-01-01T08:00:00Z 12.256708269662687 US Urban 0 2023-01-01T09:00:00Z 13.569205837415158 US Urban 0 2023-01-01T10:00:00Z 13.592033098880899 US Urban 0 2023-01-01T11:00:00Z 14.207053041454268 US Urban 0 2023-01-01T12:00:00Z 14.307481911992104 US Urban 0 2023-01-01T13:00:00Z 15.751835993369271 US Urban 0 2023-01-01T14:00:00Z 17.244567444613487 US Urban 0 2023-01-01T15:00:00Z 17.29574113958863 US Urban 0 2023-01-01T16:00:00Z 18.653968222963933 US Urban 0 2023-01-01T17:00:00Z 18.358535953764783 US Urban 0 2023-01-01T18:00:00Z 18.026725282939438 US Urban 0 2023-01-01T19:00:00Z 18.467983400521042 US Urban 0 2023-01-01T20:00:00Z 19.98355102861563 US Urban 0 2023-01-01T21:00:00Z 20.816854880851107 US Urban 0 2023-01-01T22:00:00Z 21.02060804490822 US Urban 0 2023-01-01T23:00:00Z 22.57824621147816 US Urban 0 2023-01-02T00:00:00Z 21.90593554863392 US Urban 0 2023-01-02T01:00:00Z 23.462811509194843 US Urban 0 2023-01-02T02:00:00Z 24.15522596237627 US Urban 0 2023-01-02T03:00:00Z 24.212127054158465 US Urban 0 2023-01-02T04:00:00Z 25.115157387162107 US Urban 0 2023-01-02T05:00:00Z 27.181943764903032 US Urban 0 2023-01-02T06:00:00Z 27.075731621823373 US Urban 0 2023-01-02T07:00:00Z 27.626625355558506 US Urban 0 2023-01-02T08:00:00Z 27.8543432217088 US Urban 0 2023-01-02T09:00:00Z 30.16632115848337 US Urban 0 2023-01-02T10:00:00Z 28.631927509995986 US Urban 0 2023-01-02T11:00:00Z 30.237269417893284 US Urban 0 2023-01-02T12:00:00Z 29.61891986918011 US Urban 0 2023-01-02T13:00:00Z 32.27391416346074 US Urban 0 2023-01-02T14:00:00Z 31.671074524054475 US Urban 0 2023-01-02T15:00:00Z 34.53054631594481 US Urban 0 2023-01-02T16:00:00Z 34.97239300919561 US Urban 0 2023-01-02T17:00:00Z 33.085443484625976 US Urban 0 2023-01-02T18:00:00Z 34.09871781633935 US Urban 0 2023-01-02T19:00:00Z 37.39659554160334 US Urban 0 2023-01-02T20:00:00Z 35.8292128282071 US Urban 0 2023-01-02T21:00:00Z 35.2318532191099 US Urban 0 2023-01-02T22:00:00Z 38.171362519847115 US Urban 0 2023-01-02T23:00:00Z 36.43166804169489 US Urban 0 2023-01-03T00:00:00Z 37.32768556127377 US Urban 0 2023-01-03T01:00:00Z 39.39480485947407 US Urban 0 2023-01-03T02:00:00Z 39.446810966216006 US Urban 0 2023-01-03T03:00:00Z 39.798214368249006 US Urban 0 2023-01-03T04:00:00Z 38.71715652314956 US Urban 0 2023-01-03T05:00:00Z 41.43282286119864 US Urban 0 2023-01-03T06:00:00Z 42.55790473984138 US Urban 0 2023-01-03T07:00:00Z 43.32727586393104 US Urban 0 2023-01-03T08:00:00Z 42.562410645121886 US Urban 0 2023-01-03T09:00:00Z 42.94384564294938 US Urban 0 2023-01-03T10:00:00Z 43.99939812478505 US Urban 0 2023-01-03T11:00:00Z 45.18845028599853 US Urban 0 2023-01-03T12:00:00Z 46.93004375039296 US Urban 0 2023-01-03T13:00:00Z 45.40422060036886 US Urban 0 2023-01-03T14:00:00Z 47.47486496293799 US Urban 0 2023-01-03T15:00:00Z 46.462382884678966 US Urban 0 2023-01-03T16:00:00Z 48.32922773208038 US Urban 0 2023-01-03T17:00:00Z 50.08726192149549 US Urban 0 2023-01-03T18:00:00Z 49.06978974560981 US Urban 0 2023-01-03T19:00:00Z 50.43729974841271 US Urban 0 2023-01-03T20:00:00Z 51.74496794166327 US Urban 0 2023-01-03T21:00:00Z 51.96310555211184 US Urban 0 2023-01-03T22:00:00Z 51.2922468950456 US Urban 0 2023-01-03T23:00:00Z 52.70806831687212 US Urban 0 2023-01-04T00:00:00Z 54.02470345665644 US Urban 0 2023-01-04T01:00:00Z 55.011453587449964 US Urban 0 2023-01-04T02:00:00Z 56.78892577505235 US Urban 0 2023-01-04T03:00:00Z 55.68306067026025 US Urban 0 2023-01-04T04:00:00Z 58.15090349602852 US Urban 0 2023-01-04T05:00:00Z 55.97913619486214 US Urban 0 2023-01-04T06:00:00Z 57.8863124659

##### Let's see if we can detect anomalies in the data on `2023-01-31` using AI_FORECAST().

In [0]:
WITH
-- Calcuate rollup values for each dimension
rollups AS (
  SELECT country, population, uid, ts, SUM(y) AS y
  FROM hierarchical_data_with_an_anomalous_date
  GROUP BY GROUPING SETS(
    (country, population, uid, ts),
    (country, population, ts),
    (country, ts)
  )
),
-- Get observations for the target investigation date: 2023-01-31
obs AS (SELECT * FROM rollups WHERE DATE(ts) = '2023-01-31'),
-- Calculate forcast for 2023-01-31 using historical data.
fcst AS (
  SELECT * FROM AI_FORECAST(
    TABLE(SELECT * FROM rollups WHERE ts < '2023-01-31'),
    horizon => '2023-02-01',
    time_col => 'ts',
    value_col => 'y',
    group_col => ARRAY('country', 'population', 'uid')
)
)
-- Calculate which groupings have the highest std deviation from the predicted value.
SELECT
  obs.country,
  IF(obs.population IS NULL, '[All]', obs.population) AS population,
  IF(obs.uid IS NULL, '[All]', CAST(obs.uid AS STRING)) AS uid,
  AVG(ABS(obs.y - fcst.y_forecast)) AS mean_abs_deviation
FROM
  obs
JOIN
  fcst
ON
  fcst.ts = obs.ts
  AND fcst.country <=> obs.country
  AND fcst.population <=> obs.population
  AND fcst.uid <=> obs.uid
GROUP BY
  1, 2, 3
ORDER BY
  4 DESC
LIMIT
  15


country population uid mean_abs_deviation CA Rural [All] 992.1594437690695 CA [All] [All] 968.2475200109594 CA Rural 6 176.25363546820472 CA Rural 8 145.4787203466831 CA Rural 3 119.33758635533046 CA Rural 0 118.546828737652 CA Rural 5 115.44342678249286 CA Rural 7 84.76986982108967 CA Rural 4 80.08509231715722 CA Rural 2 73.04466056147272 CA Rural 9 51.08272625670247 US [All] [All] 43.61175587048054 UK [All] [All] 41.690590805102524 IN [All] [All] 38.368677967796735 UK Suburban [All] 17.04583205849364